# Writing sample nix file for one session of spike sorted data for Monkey N

## Importing all the necessary libraries

In [1]:
import urllib

import numpy as np
import quantities as pq
from matplotlib import pyplot as plt

import neo
import nixio as nix
import elephant
from utils.plotting import Plotter
from utils.notebook import print_stats, print_metadata_table
import datetime
import odml

## Reading and exploring the blackrock data from .nev file

In [2]:
#url_path = 'https://gin.g-node.org/INT/multielectrode_grasp/raw/master/datasets/i140703-001-03.nev'
#local_path = './i140703-001-03.nev'
#urllib.request.urlretrieve(url_path, local_path)

In [3]:
#create a reader
reader = neo.io.BlackrockIO(filename="i140703-001-03.nev")
print(reader)

BlackrockIO: i140703-001-03.nev
nb_block: 1
nb_segment:  [1]
signal_channels: []
unit_channels: [ch1#0, ch1#1, ch1#2, ch2#0 ... ch95#2 ch95#3 ch96#0 ch96#1]
event_channels: [digital_input_port, serial_input_port, comments]



In [4]:
blks = reader.read(lazy=False)[0]
#Initializing an array to store all the spikestrains in each segment
train_array = []
for seg in blks.segments:
    #Extracting only the magnitde of the spike train
    train = [st.rescale('s').magnitude for st in seg.spiketrains]
    #Stacking all the spiketrains,such that,each index would give st corresponding to each unit channel
    train_array = np.hstack((train_array,train))

In [5]:
#Printing out entire reader dictionary to understand the structure of the file
for key_var , value_var in reader.header.items():
    print(key_var,value_var)

nb_block 1
nb_segment [1]
signal_channels []
unit_channels [('ch1#0', 'Unit 1000', 'uV', 0.25, 0., 10, 30000.)
 ('ch1#1', 'Unit 1001', 'uV', 0.25, 0., 10, 30000.)
 ('ch1#2', 'Unit 1002', 'uV', 0.25, 0., 10, 30000.)
 ('ch2#0', 'Unit 2000', 'uV', 0.25, 0., 10, 30000.)
 ('ch2#1', 'Unit 2001', 'uV', 0.25, 0., 10, 30000.)
 ('ch2#2', 'Unit 2002', 'uV', 0.25, 0., 10, 30000.)
 ('ch3#0', 'Unit 3000', 'uV', 0.25, 0., 10, 30000.)
 ('ch3#1', 'Unit 3001', 'uV', 0.25, 0., 10, 30000.)
 ('ch3#2', 'Unit 3002', 'uV', 0.25, 0., 10, 30000.)
 ('ch4#0', 'Unit 4000', 'uV', 0.25, 0., 10, 30000.)
 ('ch4#1', 'Unit 4001', 'uV', 0.25, 0., 10, 30000.)
 ('ch4#2', 'Unit 4002', 'uV', 0.25, 0., 10, 30000.)
 ('ch5#0', 'Unit 5000', 'uV', 0.25, 0., 10, 30000.)
 ('ch5#1', 'Unit 5001', 'uV', 0.25, 0., 10, 30000.)
 ('ch6#0', 'Unit 6000', 'uV', 0.25, 0., 10, 30000.)
 ('ch6#1', 'Unit 6001', 'uV', 0.25, 0., 10, 30000.)
 ('ch6#2', 'Unit 6002', 'uV', 0.25, 0., 10, 30000.)
 ('ch7#0', 'Unit 7000', 'uV', 0.25, 0., 10, 30000.)
 ('ch

In [6]:
#Extracting the values for key of unit channels and printing the data types
unit_channel_des = reader.header['unit_channels']
print(unit_channel_des.dtype)

[('name', '<U64'), ('id', '<U64'), ('wf_units', '<U64'), ('wf_gain', '<f8'), ('wf_offset', '<f8'), ('wf_left_sweep', '<i8'), ('wf_sampling_rate', '<f8')]


In [7]:
#Defining a function to extact fields corresponding to the field name from a ndarray
def fields_view(arr, fields):
    dtype2 = np.dtype({name:arr.dtype.fields[name] for name in fields})
    return np.ndarray(arr.shape, dtype2, arr, 0, arr.strides)

In [8]:
#Extracting all the fields of unit channel key using fields_view() function
channel_name = fields_view(unit_channel_des, ["name"])
channel_id = fields_view(unit_channel_des, ["id"])
channel_wf_units = fields_view(unit_channel_des, ["wf_units"])
channel_wf_gain = fields_view(unit_channel_des, ["wf_gain"])
channel_wf_offset = fields_view(unit_channel_des, ["wf_offset"])
channel_wf_left_sweep = fields_view(unit_channel_des, ["wf_left_sweep"])
channel_wf_sampling_rate = fields_view(unit_channel_des, ["wf_sampling_rate"])

## Creating a nix file and adding some Data available

In [9]:
#Opening a nix file
nixfile = nix.File.open("test_nix.h5", nix.FileMode.Overwrite)

In [10]:
#Creating blocks corresponding to each key of the reader dictionary of .nev file
block = nixfile.create_block("nb_block", "nix.block")
block_seg = nixfile.create_block("nb_segment","nix.segment")
block_sig = nixfile.create_block("signal_channels", "nix.signal_channels")
block_unit = nixfile.create_block("unit_channels", "nix.unit_channels")
block_event = nixfile.create_block("event_channels", "nix.event_channels")

In [11]:
#Counting and printing the total number of unit channels
total_units = reader.unit_channels_count()
print("Total number of units :",total_units)

#Iterating over each channel,to populate the unit_channels block with available information
for unit_index in range(total_units):
    
    channel_name_str = str((channel_id[unit_index])[0])
    data = block_unit.create_data_array(channel_name_str,"session.unit_channel",data=[])
    
    data.wf_units = str((channel_wf_units[unit_index])[0])
    data.wf_gain = str((channel_wf_gain[unit_index])[0])
    data.wf_offset = str((channel_wf_offset[unit_index])[0])
    data.wf_left_sweep = str((channel_wf_left_sweep[unit_index])[0])
    data.wf_sampling_rate = str((channel_wf_sampling_rate[unit_index])[0])    
    
    

Total number of units : 271


In [12]:
#Printing all the blocks types and how many are there of each type
print_stats(nixfile.blocks)


Blocks                                             (05)
	type: nix.block                            (01)
	type: nix.unit_channels                    (01)
	type: nix.signal_channels                  (01)
	type: nix.segment                          (01)
	type: nix.event_channels                   (01)


In [13]:
#Printing the type and number of data array if available in each block
print_stats(block.data_arrays)
print_stats(block_seg.data_arrays)
print_stats(block_sig.data_arrays)
print_stats(block_unit.data_arrays)
print_stats(block_event.data_arrays)


DataArrays                                         (271)
	type: session.unit_channel                 (271)


In [14]:
#Iterating over each channel,to populate the segment block with spike train data
for unit_index in range(total_units):
    channel_name_str = str((channel_id[unit_index])[0])
    data = block_seg.create_data_array(channel_name_str,"segment.spike_train",data=train_array[unit_index])
    data.label = "Spike_Train"
    data.unit = 's'

## Adding some metadata to the nix file

In [15]:
#Extracting some metadata in the form of attributes using elephant
elephant.neo_tools.extract_neo_attributes(blks)

{'avail_file_set': ['nev'],
 'avail_nsx': [],
 'avail_nev': True,
 'rec_pauses': False,
 'file_datetime': None,
 'rec_datetime': datetime.datetime(2014, 7, 3, 10, 40, 59, 288),
 'index': None,
 'name': 'Blackrock Data Block',
 'description': 'Block of data from Blackrock file set.',
 'file_origin': 'i140703-001-03.nev'}

In [16]:
#Adding the metadata associated with the nb_block
attribute_data = nixfile.create_section("nb_block", "nix.block")
attribute_data["Available_File_Set"] = ".nev"
attribute_data["Recording_Date_Time"] = str(datetime.datetime(2014, 7, 3, 10, 40, 59, 288))
attribute_data["Name"] = "Blackrock Data Block"
attribute_data["Description"] = "Block of data from Blackrock file set."
attribute_data["File_Origin"] = "i140703-001-03.nev"


In [17]:
#Loading the associated odml file for the session
odml_load = odml.load("i140703-001.odml")

warning[None:17:<{http://www.w3.org/1999/xsl/transform}stylesheet>]: Invalid element <{http://www.w3.org/1999/xsl/transform}stylesheet> inside <odML> tag
 (line 17)
warning[None:17:<{http://www.w3.org/1999/xsl/transform}stylesheet>]: Invalid element <{http://www.w3.org/1999/xsl/transform}stylesheet> in odML document section <odML>  (line 17)
Validation found 0 errors and 3 warnings in 0 Sections and 3 Properties.


In [18]:
odml_load

Document 0.1 {author = Lyuba Zehl, 8 sections}

In [19]:
#Printing all the the sections and properties from the odml file using pprint
odml_load.pprint()

[Lyuba Zehl [0.1] 2017-07-14, sections: 8, repository: None]
   Setup [setup]
      |- Location: ['Inst. de Neurosciences de la Timone (I ... Aix Marseille Univ., Marseille, France']
      |- DAQSystem: ['Cerebus']
     Apparatus [setup]
       [...]
   Subject [subject]
      |- Species: ['Macaca mulatta']
      |- TrivialName: ['Rhesus monkey']
      |- GivenName: ['monkey_N']
      |- Identifier: ['i']
      |- Gender: ['male']
      |- Birthday: [datetime.date(2008, 5, 17)]
      |- ActiveHand: ['left']
      |- Disabilities: ['-']
      |- Character: ['Calm, but overall not really motivated. Less attentive.']
     Training [subject/preparation]
       [...]
     ArrayImplant [subject/preparation]
       [...]
   Project [project]
      |- Name: ['reach-to-grasp']
      |- Type: ['electrophysiology']
      |- Subtype: ['motor behavior']
      |- Collaborators: ['Inst. of Neuroscience and Medicine (INM- ... Marseille Univ.', ' Marseille', ' France']
     TaskDesigns [project]
      

In [20]:
#Adding some metadata manually and associating it with the nb_segment block
Recording_metadata = nixfile.create_section("nb_segment","nix.segment")
Recording_metadata["RecordingDay"] = "i140703"
Recording_metadata["Recording"] = "i140703-001"
Recording_metadata["Date"] = str(datetime.date(2014, 7, 3))
Recording_metadata["Weekday"] = "Thursday"
Recording_metadata["Duration"] = "1003_seconds"
Recording_metadata["IsSpikeSorted"] = "True"
Recording_metadata["TaskType"] = "TwoCues"


In [21]:
#Adding source for the data in the segment block
source = block_seg.create_source("monkey_N", "nix.experimental_subject")

In [22]:
#Adding some subject metadata
subject = Recording_metadata.create_section("monkey_N", "nix.experimental_subject")
subject["Species"] = "Macaca mulatta"
subject["TrivialName"] = "Rhesus monkey"
subject["Identifier"] = 'i'

In [23]:
nixfile.close()